In [1]:
import hashlib
import os
import shutil
import subprocess
import uuid
from typing import Optional, List
import gzip
import json
from multiprocessing.pool import ThreadPool

import pandas as pd
import requests
from cooler import Cooler
from pydantic import BaseModel

In [2]:
class HiCExperiment(BaseModel):
    """A class to represent a Hi-C experiment"""

    accession: Optional[str] = None
    assay_term_name: Optional[str] = None
    assay_title: Optional[str] = None
    award: Optional[dict] = None
    biosample: Optional[str] = None
    biosample_ontology: Optional[dict] = None
    biosample_summary: Optional[str] = None
    dbxrefs: Optional[list] = None
    description: Optional[str] = None
    lab: Optional[dict] = None
    replicates: Optional[list] = None
    status: Optional[str] = None
    hic_accession: Optional[str] = None

    def __repr__(self):
        return f"{self.biosample_summary} - {self.accession}: {self.hic_accession}"


class HiCExperimentList(BaseModel):
    experiments: List[HiCExperiment]


def download_encode(accession, extension):
    """Download an ENCODE file by its accession and store the result on disk"""
    url = f"https://www.encodeproject.org/files/{accession}/@@download/{accession}.{extension}"
    local_filename = f"/net/common/cache/encode/GRCh38/{accession}.{extension}"
    if os.path.exists(local_filename):
        return local_filename
    with requests.get(url, stream=True, allow_redirects=True) as r:
        temp_file = str(uuid.uuid4()) + f".{extension}"
        print(f"Downloading {accession} to {temp_file}")
        with open(temp_file, "wb") as f:
            shutil.copyfileobj(r.raw, f)
        shutil.move(temp_file, local_filename)
    return local_filename


def verify_encode_file(accession, extension):
    """Verify md5 checksum of encode file"""
    url = f"https://www.encodeproject.org/files/{accession}/?format=json"
    response = requests.get(url)
    payload = response.json()
    md5sum = payload["md5sum"]
    local_filename = download_encode(accession, extension)

    # Get md5sum of file
    with open(local_filename, "rb") as f:
        file_hash = hashlib.md5()
        while chunk := f.read(67108864):  # 64 MB chunks
            file_hash.update(chunk)
        file_md5sum = file_hash.hexdigest()

    # Check md5sum matches
    if md5sum != file_md5sum:
        os.remove(local_filename)
        print(f"MD5 checksums don't match for {accession}!")
        raise Exception(f"MD5 checksums don't match for {accession}!")
    print(f"Verified MD5 checksum for {accession}.{extension}")
    return local_filename


def hic_to_mcool(accession):
    """Convert a hic file to a mcool file"""
    mcool_file = f"{accession}.mcool"
    if os.path.exists(mcool_file):
        try:
            clr = Cooler(f"{mcool_file}::/resolutions/50000")
            print(clr.info)
            return mcool_file
        except OSError as e:
            os.remove(mcool_file)
            raise e

    hic_file = verify_encode_file(accession, "hic")
    temp_name = str(uuid.uuid4())
    temp_hic = f"{temp_name}.hic"
    temp_mcool = f"{temp_name}.mcool"
    shutil.copy(hic_file, temp_hic)
    subprocess.run(["/home/reimonnt/miniconda3/envs/hictk/bin/hictk", "convert", temp_hic, temp_mcool], capture_output=False)
    shutil.move(temp_mcool, mcool_file)
    os.remove(temp_hic)
    return mcool_file

In [3]:
primary_cell = pd.read_csv("metadata-primary-cell-samples.csv")
tissues = pd.read_csv("metadata-tissue-samples.csv")

In [4]:
metadata = pd.concat([primary_cell, tissues])
metadata.head()

Unnamed: 0    accession assay_term_name   assay_title  \
0          10  ENCSR711AVS             HiC  in situ Hi-C   
1          14  ENCSR351NAI             HiC   intact Hi-C   
2          17  ENCSR923PPH             HiC   intact Hi-C   
3          22  ENCSR456QYU             HiC   intact Hi-C   
4          27  ENCSR236EYO             HiC   intact Hi-C   

                   award                                  biosample  \
0  {'project': 'ENCODE'}                    mammary epithelial cell   
1  {'project': 'ENCODE'}  activated CD8-positive, alpha-beta T cell   
2  {'project': 'ENCODE'}  activated CD4-positive, alpha-beta T cell   
3  {'project': 'ENCODE'}                             dendritic cell   
4  {'project': 'ENCODE'}                     CD14-positive monocyte   

                                  biosample_ontology  \
0  {'term_name': 'mammary epithelial cell', 'clas...   
1  {'term_name': 'activated CD8-positive, alpha-b...   
2  {'term_name': 'activated CD4-positive, alpha-b...   
3  {'term_name': 'dendritic cell', 'classificatio...   
4  {'term_name': 'CD14-positive monocyte', 'class...   

                                   biosample_summary            dbxrefs  \
0               Homo sapiens mammary epithelial cell                 []   
1  Homo sapiens activated CD8-positive, alpha-bet...  ['GEO:GSE237357']   
2  Homo sapiens activated CD4-positive, alpha-bet...  ['GEO:GSE238027']   
3  Homo sapiens dendritic cell male adult (51 yea...  ['GEO:GSE237482']   
4  Homo sapiens CD14-positive monocyte male adult...  ['GEO:GSE237421']   

                                         description  ...        format  \
0                       HMEC in situ Hi-C experiment  ...  HDF5::Cooler   
1                         CD8+ activated intact Hi-C  ...  HDF5::Cooler   
2  naive CD4+ T cell  Th0 effector _activated int...  ...  HDF5::Cooler   
3  Monocytes Dendritic cell day 4 LP23 intact mna...  ...  HDF5::Cooler   
4                              Monocytes intact Hi-C  ...  HDF5::Cooler   

                         format-url format-version            generated-by  \
0  https://github.com/open2c/cooler              3  hictk-v0.0.10-bioconda   
1  https://github.com/open2c/cooler              3  hictk-v0.0.10-bioconda   
2  https://github.com/open2c/cooler              3  hictk-v0.0.10-bioconda   
3  https://github.com/open2c/cooler              3  hictk-v0.0.10-bioconda   
4  https://github.com/open2c/cooler              3  hictk-v0.0.10-bioconda   

  metadata  nbins nchroms        nnz     storage-mode         sum  
0       {}  61776      25  304004037  symmetric-upper  1286376999  
1       {}  61776      25  281321644  symmetric-upper  1009581526  
2       {}  61776      25  637408941  symmetric-upper  1577549156  
3       {}  61776      25  371618574  symmetric-upper  1161869581  
4       {}  61776      25  417065358  symmetric-upper  1100063813  

[5 rows x 33 columns]

In [5]:
accessions = metadata.hic_accession.to_list()
print(f"Number of accessions: {len(accessions)}")

Number of accessions: 73


In [6]:
# accessions

In [ ]:
# Download files
with ThreadPool(16) as pool:
    mcool_filelist = pool.map(hic_to_mcool, accessions)

Verified MD5 checksum for ENCFF654YIQ.hic


[2024-09-10 11:06:09.491] [info]: Running hictk v1.0.0-bioconda
[2024-09-10 11:06:09.492] [info]: Converting cebe062e-5348-4498-aa61-8f5ef7e46279.hic to cebe062e-5348-4498-aa61-8f5ef7e46279.mcool (hic -> mcool)...
[2024-09-10 11:06:15.373] [info]: [100] begin processing 100bp matrix...
[2024-09-10 11:06:34.497] [info]: [100] processing chr1:22064200-22064300 at 523040 pixels/s (cache hit rate 0.00%)...
[2024-09-10 11:06:42.576] [info]: [100] processing chr1:42851400-42851500 at 1237930 pixels/s (cache hit rate 0.02%)...
[2024-09-10 11:06:51.663] [info]: [100] processing chr1:63329300-63329400 at 1100594 pixels/s (cache hit rate 0.00%)...
[2024-09-10 11:07:00.773] [info]: [100] processing chr1:85668400-85668500 at 1097695 pixels/s (cache hit rate 0.00%)...
[2024-09-10 11:07:08.980] [info]: [100] processing chr1:110274600-110274700 at 1218621 pixels/s (cache hit rate 0.00%)...
[2024-09-10 11:07:16.777] [info]: [100] processing chr1:161715200-161715300 at 1282709 pixels/s (cache hit rate 

Verified MD5 checksum for ENCFF943JRY.hic


[2024-09-10 11:09:42.704] [info]: [100] processing chr3:197551300-197551400 at 2748763 pixels/s (cache hit rate 0.00%)...
[2024-09-10 11:10:04.896] [info]: [100] processing chr4:22470400-22470500 at 450633 pixels/s (cache hit rate 0.01%)...
[2024-09-10 11:10:12.925] [info]: [100] processing chr4:46229600-46229700 at 1245485 pixels/s (cache hit rate 0.00%)...
[2024-09-10 11:10:21.425] [info]: [100] processing chr4:73738700-73738800 at 1176609 pixels/s (cache hit rate 0.00%)...
[2024-09-10 11:10:28.390] [info]: [100] processing chr4:98487500-98487600 at 1435750 pixels/s (cache hit rate 0.00%)...
[2024-09-10 11:10:34.812] [info]: [100] processing chr4:125394100-125394200 at 1557390 pixels/s (cache hit rate 0.03%)...
[2024-09-10 11:10:40.071] [info]: [100] processing chr4:153160500-153160600 at 1901864 pixels/s (cache hit rate 0.00%)...
[2024-09-10 11:10:42.289] [info]: Running hictk v1.0.0-bioconda
[2024-09-10 11:10:42.289] [info]: Converting 98c75b2e-5f32-42e0-bc8e-059a4bb4da9a.hic to 98

[2024-09-10 11:17:30.347] [info]: [100] processing chr9:100890100-100890200 at 2336449 pixels/s (cache hit rate 0.00%)...
[2024-09-10 11:17:33.951] [info]: [100] processing chr9:124946400-124946500 at 2774695 pixels/s (cache hit rate 0.00%)...
[2024-09-10 11:17:42.259] [info]: [100] processing chr10:9790600-9790700 at 1203804 pixels/s (cache hit rate 0.03%)...
[2024-09-10 11:17:47.911] [info]: [100] processing chr10:31914700-31914800 at 1769598 pixels/s (cache hit rate 0.00%)...
[2024-09-10 11:17:53.872] [info]: [100] processing chr10:61607000-61607100 at 1677571 pixels/s (cache hit rate 0.00%)...
[2024-09-10 11:17:58.666] [info]: [100] processing chr10:84867700-84867800 at 2086376 pixels/s (cache hit rate 0.00%)...
[2024-09-10 11:18:02.680] [info]: [100] processing chr10:108917300-108917400 at 2491901 pixels/s (cache hit rate 0.00%)...
[2024-09-10 11:18:09.583] [info]: [100] processing chr11:1698800-1698900 at 1448646 pixels/s (cache hit rate 0.12%)...
[2024-09-10 11:18:16.091] [info]

Verified MD5 checksum for ENCFF783KQI.hic


[2024-09-10 11:35:29.203] [info]: Running hictk v1.0.0-bioconda
[2024-09-10 11:35:29.203] [info]: Converting c9144acd-ec6d-40ec-bb7b-6737b7463167.hic to c9144acd-ec6d-40ec-bb7b-6737b7463167.mcool (hic -> mcool)...
[2024-09-10 11:36:15.403] [info]: [10] begin processing 10bp matrix...
[2024-09-10 11:36:39.096] [info]: [10] processing chr1:20362050-20362060 at 422155 pixels/s (cache hit rate 0.00%)...
[2024-09-10 11:36:47.205] [info]: [10] processing chr1:38924630-38924640 at 1233350 pixels/s (cache hit rate 0.02%)...
[2024-09-10 11:36:56.070] [info]: [10] processing chr1:56824170-56824180 at 1128032 pixels/s (cache hit rate 0.00%)...
[2024-09-10 11:37:03.446] [info]: [10] processing chr1:73105490-73105500 at 1355932 pixels/s (cache hit rate 0.00%)...
[2024-09-10 11:37:11.829] [info]: [10] processing chr1:91231630-91231640 at 1192890 pixels/s (cache hit rate 0.00%)...
[2024-09-10 11:37:18.800] [info]: [10] processing chr1:112956860-112956870 at 1434720 pixels/s (cache hit rate 0.00%)...
